# Visualising the database using iGraph

In [1]:
import i graph
import py2neo
import matplotlib.pyplot as plt
import networkx as nx

In [2]:
def query_database(query):
    # REMEMBER TO BE CONNECTED TO IMPERIAL WIFI!
    graph_db = py2neo.Graph("https://dsi-bitcoin.doc.ic.ac.uk:7473/db/data/", auth=("guest_ro", "imperialO_nly"))
    return graph_db.run(query)

def get_block_data(first_block, last_block):
    query_string = """
                    MATCH (b:Block) <-[:MINED_IN]- (t:Tx) <-[:IN]- (txi:TxIn) <-[:UNLOCK]- (iadr:Address)
                    WHERE b.height >= {} AND b.height <= {}
                    MATCH (txi) <-[:SPENT]- (txo_in:TxOut) 
                    MATCH (oadr:Address) <-[:LOCK]- (txo_out:TxOut) <-[:OUT]- (t)
                    
                    RETURN iadr.address as iadr, oadr.address as oadr, txo_in.value as input_val, txo_out.value as output_val, ID(txo_in) as id_txo_in, ID(txi) as id_txi, ID(t) as id_t, ID(txo_out) as id_txo_out
                    """.format(first_block, last_block)
    return query_string

In [3]:
result = query_database(get_block_data(400000,400000))

tups1 = []
tups2 = []
for d in result:
    tups1.append((d['iadr'],d['oadr']))
   

In [5]:
ig = igraph.Graph.TupleList(tups1,directed=True,vertex_name_attr='label',edge_attrs=['weight'])

visual_style = {}
visual_style["vertex_size"] = 0.5
visual_style["layout"] = "fr"

igraph.plot(ig,**visual_style)

In [ ]:
ig = igraph.Graph.TupleList(tups1,directed=True,vertex_name_attr='label',edge_attrs=['weight'])

layout = ig.layout_kamada_kawai()
visual_style = {}
visual_style["layout"] = layout
visual_style["bbox"]= (8000, 8000)
visual_style["margin"] = 10
visual_style["autocurve"] = True
visual_style["vertex_label"] = ig.vs['label']
visual_style["arrow_size"] = 0.5
visual_style["arrow_size"] = 0.5
size = []
for i in ig.degree():
    if i > 1:
        size.append(20*log(i))
    else:
        size.append(i)
visual_style["vertex_size"] = size
print(ig.indegree())
print(type(ig.indegree()))
igraph.plot(ig,**visual_style)

## Finding users by using heuristic measures

In [ ]:
from collections import defaultdict

users_dict = defaultdict(lambda: {'iadr': set(), 'oadr': set()})
address_dict = defaultdict(lambda: {'user':set()})

In [ ]:
#CHANGE LATER TO QUERY DATABASE INSTEAD
def iadrs_from_tx(id_t):
    return set(df['iadr'][df["id_t"] == id_t])

def oadrs_from_tx(id_t):
    return set(df['oadr'][df["id_t"] == id_t])

def tx_from_iadr(iadr):
    return set(df['id_t'][df["iadr"] == iadr])

#FUNCTION TO WHICH YOU GIVE AN INPUT ADDRESS AND GET USER 
def get_user(input_adr):
    to_inv = [input_adr]
    user_iadrs = set()
    seen_txs = set()
    while to_inv:
        current_iadr = to_inv.pop(0)
        user_iadrs.add(current_iadr)
        for id_t in tx_from_iadr(current_iadr):

            if id_t not in seen_txs:
                
                seen_txs.add(id_t)
                iadrs = iadrs_from_tx(id_t)
                to_inv += iadrs.difference(user_iadrs) #Adding addr
                user_iadrs.update(iadrs)
            
    return User(user_iadrs, seen_txs)

#LIST OF LISTS OF USER AND THEIR ASSOCIATED ADDRESSES
users = []

class User:
    def __init__(self, iadrs, txs):
        self.iadr = set(iadrs)
        self.tx = set(txs)
        self.cadr = set()
        

#ASSOCIATE INPUT ADDRESS AND TX WITH EACH USER IN BLOCK
already_seen_iadr = set()
for input_adr in df.iadr:
    if input_adr not in already_seen_iadr:
        user = get_user(input_adr)
        users.append(user)
        already_seen_iadr.update(user.iadr)

#TAKES OUTPUT ADDRESS AND GIVES USER THAT HAS THAT ADDRESS AS INPUT
def user_from_oadr(oadr):
    for i,user in enumerate(users):
        if oadr in user.iadr:
            return i
        
edges = defaultdict(int)

#WHICH USERS IN HAVE TRANSACTED WITH EACH OTHER
for i,user in enumerate(users):
    for tx_id in user.tx:
        for oadr in oadrs_from_tx(tx_id):
            if oadr in already_seen_iadr:
                if(i!=user_from_oadr(oadr)):
                    edges[(i, user_from_oadr(oadr))]+=1  
            

In [ ]:
for i,user in enumerate(users):
    for tx_id in user.tx:
        o = oadrs_from_tx(tx_id)
        if not user.iadr.intersection(o):
            adr_found = None
            for oadr in o:
                if not seen_before(400000, str(oadr)):
                    if adr_found:
                        ch_addr = None
                        break
                    else:
                        ch_addr = oadr
            if ch_addr:
                user.cadr.add(ch_addr)

In [ ]:
addresses1 = list(df.oadr.value_counts()[df.oadr.value_counts()>1].index)
addresses2 = list(df.oadr.value_counts()[df.oadr.value_counts()==1].index)

In [ ]:
addresses = list(df.oadr.value_counts().index)

In [ ]:
blk = 400000

not_seen =[]
import time

temptime = 0
starttime = 0

for adr in addresses:
    if seen_before1(blk, adr) or seen_before2(blk, adr):
        continue
    else:
        not_seen.append(adr)
    print(adr, " processed in ", time.time()-temptime)
    temptime = time.time()
    
print("Total time to process: ", time.time()-starttime)

In [ ]:
import pickle
with open('file.txt','wb') as f:
    pickle.dump(not_seen,f)

In [ ]:
blk = 400000
not_seen = [adr for adr in addresses1[:5] if not seen_before1(blk, adr) and not seen_before2(blk, adr)]

In [ ]:
import collections as c

count = c.defaultdict(int) 

for user in users:
    count[len(user)]+=1

In [ ]:
plt.plot(count.keys(),count.values())

In [ ]:
matches = set(df.iadr).intersection(df.oadr)
print(matches)

In [ ]:
ig2 = igraph.Graph.TupleList(tups2, vertex_name_attr = 'tx')
g.vs['out'] = 
igraph.plot(ig2,**visual_style)

In [ ]:
g = igraph.Graph()

In [ ]:
g.add_edge('A','B',weight = 20)

In [ ]:
#Insert Transactions and value of each transaction into graph

g.add_vertices(txo_out_ids)
g.add_vertices(txo_in_ids)

In [ ]:
len(txo_out_ids)
len(tx_ids)
len(txo_in_ids)
g.vcount()
g.vs[3]

In [ ]:
#Insert tx inputs into graph
g.add_vertices(txo_in_ids)
g.vs["type"] = 'in'
g.vs["in_ids"] = txo_in_ids
try:
    del g.vs["name"]
except Exception: 
  pass  

In [ ]:
#Insert tx outputs into graph
g.add_vertices(txo_out_ids)
g.vs["type"] = 'out'
g.vs["out_ids"] = txo_out_ids
try:
    del g.vs["name"]
except Exception: 
  pass    

In [ ]:
color_dict = {"tx": "green", "in": "orange", "out":'blue'}

In [ ]:
visual_style = {}
visual_style["vertex_size"] = 2
visual_style["layout"] = "fr"
visual_style["vertebx_color"] = [color_dict[type] for type in g.vs["type"]]

In [ ]:
igraph.plot(g, **visual_style)

In [ ]:
tx_id = []
for i in df.index():
    edge = (df.ix[i, 'name1'], df.ix[i, 'name2'])
    if edge not in edgelist:
        edgelist.append(edge)
        weights.append(1)
    else:
        weights[edgelist.index(edge)] += 1

G = Graph()
G.add_edges(edgelist)
G.es['weight'] = weights